Lectura de xml

In [1]:
import pandas as pd
import xml.etree.ElementTree as etree


tree = etree.parse("pu-cs-fal07.xml")
#tree = etree.parse("lums-sum17.xml")
root = tree.getroot()

columns_problem = ["Name", "NrDays", "SlotsPerDay", "NrWeeks"]
columns_optimization = ["Time", "Room", "Distribution", "Student"]
columns_rooms = ["RoomId", "Capacity", "PreviousRoomIdList", "TravelTimeValueList", "UnavailableDaysList", "UnavailableStartList", "UnavailableLengthList", "UnavailableWeeksList"]
columns_courses = ["CourseId", "ConfigIdList"]
columns_configs = ["ConfigId", "SubpartIdList"]
columns_subparts = ["SubpartId", "ClassIdList"]
columns_classes = ["ClassId", "ClassLimit", "ClassParent"]
columns_distributions = ["DistributionId", "DistributionType", "DistributionRequired", "DistributionPenalty", "ClassesList"]
columns_students = ["StudentId", "CoursesList"]
columns_relation_class_room = ["ClassId", "RoomId", "RoomPenalty"]
columns_relation_class_time = ["ClassId", "TimeDays", "TimeStart", "TimeLength", "TimeWeeks", "TimePenalty"]

df_problem = pd.DataFrame(columns = columns_problem)
df_optimization = pd.DataFrame(columns = columns_optimization)
df_rooms = pd.DataFrame(columns = columns_rooms)
df_courses = pd.DataFrame(columns = columns_courses)
df_configs = pd.DataFrame(columns = columns_configs)
df_subparts = pd.DataFrame(columns = columns_subparts)
df_classes = pd.DataFrame(columns = columns_classes)
df_distributions = pd.DataFrame(columns = columns_distributions)
df_students = pd.DataFrame(columns = columns_students)
df_relation_class_room = pd.DataFrame(columns = columns_relation_class_room)
df_relation_class_time = pd.DataFrame(columns = columns_relation_class_time)




df_problem = df_problem.append({"Name": root.attrib.get("name"), "NrDays": root.attrib.get("nrDays"), "SlotsPerDay": root.attrib.get("slotsPerDay"), "NrWeeks": root.attrib.get("nrWeeks")}, ignore_index = True)

for node in root:
    if node.tag == "optimization":
        df_optimization = df_optimization.append({"Time": node.attrib.get("time"), "Room": node.attrib.get("room"), "Distribution": node.attrib.get("distribution"), "Student": node.attrib.get("student")}, ignore_index = True)
    
    elif node.tag == "rooms":
        for room in node:
            roomid = room.attrib.get("id")
            cap = room.attrib.get("capacity")
            prevroomlist = []
            valuelist = []
            dayslist = []
            startlist = []
            lengthlist = []
            weekslist = []
            if len(list(child.tag for child in room.iter() if child is not room)) > 0:
                for child in room:
                    if child.tag == "travel":
                        prevroomid = child.attrib.get("room")
                        value = child.attrib.get("value")
                        prevroomlist.append(prevroomid)
                        valuelist.append(value)
                    elif child.tag == "unavailable":
                        days = child.attrib.get("days")
                        start = child.attrib.get("start")
                        length = child.attrib.get("length")
                        weeks = child.attrib.get("weeks")
                        dayslist.append(days)
                        startlist.append(start)
                        lengthlist.append(length)
                        weekslist.append(weeks)
            if len(prevroomlist) == 0:
                prevroomlist = None
            if len(valuelist) == 0:
                valuelist = None
            if len(dayslist) == 0:
                dayslist = None
            if len(startlist) == 0:
                startlist = None
            if len(lengthlist) == 0:
                lengthlist = None
            if len(weekslist) == 0:
                weekslist = None
            df_rooms = df_rooms.append(pd.Series([roomid, cap, prevroomlist, valuelist, dayslist, startlist, lengthlist, weekslist], index = columns_rooms), ignore_index = True)
            
    elif node.tag == "courses":
        for course in node:
            #print(course.tag)
            courseid = course.attrib.get("id")
            configlist = []
            for config in course:
                #print(config.tag)
                configid = config.attrib.get("id")
                configlist.append(configid)
                subpartlist = []
                for subpart in config:
                    #print(subpart.tag)
                    subpartid = subpart.attrib.get("id")
                    subpartlist.append(subpartid)
                    claselist = []
                    for clase in subpart:
                        #print(clase.tag)
                        claseid = clase.attrib.get("id")
                        claselist.append(claseid)
                        claselimit = clase.attrib.get("limit")
                        claseparent = clase.attrib.get("parent") if clase.attrib.get("parent") is not None else None
                        df_classes = df_classes.append(pd.Series([claseid, claselimit, claseparent], index = columns_classes), ignore_index = True)
                        if len(list(child.tag for child in clase.iter() if child is not clase)) > 0:
                            for child in clase:
                                #print(child.tag)
                                if child.tag == "room":
                                    roomid = child.attrib.get("id")
                                    roompenalty = child.attrib.get("penalty")
                                    df_relation_class_room = df_relation_class_room.append(pd.Series([claseid, roomid, roompenalty], index = columns_relation_class_room), ignore_index = True)
                                elif child.tag == "time":
                                    timedays = child.attrib.get("days")
                                    timestart = child.attrib.get("start")
                                    timelength = child.attrib.get("length")
                                    timeweeks = child.attrib.get("weeks")
                                    timepenalty = child.attrib.get("penalty")
                                    df_relation_class_time = df_relation_class_time.append(pd.Series([claseid, timedays, timestart, timelength, timeweeks, timepenalty], index = columns_relation_class_time), ignore_index = True)
                    df_subparts = df_subparts.append(pd.Series([subpartid, claselist], index = columns_subparts), ignore_index = True)
                df_configs = df_configs.append(pd.Series([configid, subpartlist], index = columns_configs), ignore_index = True)
            df_courses = df_courses.append(pd.Series([courseid, configlist], index = columns_courses), ignore_index = True)
                                    
    elif node.tag == "distributions":
        contador = 1
        for distribution in node:
            #print(distribution.tag)
            distribid = contador
            distribtype = distribution.attrib.get("type")
            distribrequired = distribution.attrib.get("required") if distribution.attrib.get("required") is not None else None
            distribpenalty = distribution.attrib.get("penalty") if distribution.attrib.get("penalty") is not None else None
            listaclases = []
            for clase in distribution:
                #print(clase.tag)
                listaclases.append(clase.attrib.get("id"))
            df_distributions = df_distributions.append(pd.Series([distribid, distribtype, distribrequired, distribpenalty, listaclases], index = columns_distributions), ignore_index = True)
            contador += 1
             
    elif node.tag == "students":
        for student in node:
            studentid = student.attrib.get("id")
            listacourses = []
            for course in student:
                listacourses.append(course.attrib.get("id"))
            df_students = df_students.append(pd.Series([studentid, listacourses], index = columns_students), ignore_index = True)
            
            


print("################################################################################################################")
print("DataFrame Problem")
display(df_problem)
print("################################################################################################################")
print("DataFrame Optimization")
display(df_optimization)
print("################################################################################################################")
print("DataFrame Rooms")
display(df_rooms)
print("################################################################################################################")
print("DataFrame Courses")
display(df_courses)
print("################################################################################################################")
print("DataFrame Configs")
display(df_configs)
print("################################################################################################################")
print("DataFrame Subparts")
display(df_subparts)
print("################################################################################################################")
print("DataFrame Classes")
display(df_classes)
print("################################################################################################################")
print("DataFrame Distributions")
display(df_distributions)
print("################################################################################################################")
print("DataFrame Students")
display(df_students)
print("################################################################################################################")
print("DataFrame RelationClassRoom")
display(df_relation_class_room)
print("################################################################################################################")
print("DataFrame RelationClassTime")
display(df_relation_class_time)
print("################################################################################################################")

################################################################################################################
DataFrame Problem


Name NrDays SlotsPerDay NrWeeks
0  pu-cs-fal07      7         288      15

################################################################################################################
DataFrame Optimization


Time Room Distribution Student
0    1    1           10      10

################################################################################################################
DataFrame Rooms


...

################################################################################################################
DataFrame RelationClassRoom


ClassId RoomId RoomPenalty
0         1     10           0
1         1     11           0
2         1     12           0
3         2     10           0
4         2     11           0
..      ...    ...         ...
385     173      2           0
386     173      3           0
387     174      1          44
388     174      2           0
389     174      3           0

[390 rows x 3 columns]

################################################################################################################
DataFrame RelationClassTime


ClassId TimeDays TimeStart TimeLength        TimeWeeks TimePenalty
0          1  0100000        90         22  111111111111111           0
1          1  0010000        90         22  111111111111111           0
2          1  0001000        90         22  111111111111111           0
3          1  0000100        90         22  111111111111111           0
4          1  0100000       114         22  111111111111111           0
...      ...      ...       ...        ...              ...         ...
2953     174  0101000       186         10  111111110000000          16
2954     174  1010000       198         10  111111110000000          16
2955     174  1000100       198         10  111111110000000          16
2956     174  0101000       198         10  111111110000000          16
2957     174  0010100       198         10  111111110000000          16

[2958 rows x 6 columns]

################################################################################################################


Analisis de datos

In [2]:
## Duracion en slots de clases:

df_relation_class_time["TimeLength"] = df_relation_class_time["TimeLength"].astype(int)
print("Promedio:")
display(df_relation_class_time["TimeLength"].mean())
print("Min:")
display(df_relation_class_time["TimeLength"].min())
print("Max:")
display(df_relation_class_time["TimeLength"].max())
print("Tiempo de inicio")
display(df_relation_class_time.groupby("TimeStart").count())
x = df_relation_class_time.groupby("TimeStart").count()
print("Count")
display(df_relation_class_time["TimeLength"].value_counts())
print("Mediana:")
display(df_relation_class_time["TimeLength"].median())
print("Cuartiles:")
display(df_relation_class_time["TimeLength"].quantile([0, 0.25, 0.5, 0.75, 1]))
print("Var:")
display(df_relation_class_time["TimeLength"].var())
print("Std:")
display(df_relation_class_time["TimeLength"].std())

Promedio:


18.17816091954023

Min:


10

Max:


...

0.00    10.0
0.25    10.0
0.50    22.0
0.75    22.0
1.00    22.0
Name: TimeLength, dtype: float64

Var:


29.62093648812983

Std:


5.442511964904609

In [3]:
##SPFf=subpartes de la configuracion f
#Cantidad de subpartes de una configuración
dicc_SPFf = {}
for index, col in df_configs.iterrows():
    dicc_SPFf[col["ConfigId"]] = [int(x) for x in col["SubpartIdList"]]
print(dicc_SPFf)


{'1': [1], '2': [2, 3], '3': [4], '4': [5, 6], '5': [7, 8], '6': [9, 10], '7': [11], '8': [12, 13], '9': [14, 15], '10': [16, 17], '11': [18, 19], '12': [20, 21], '13': [22, 23], '14': [24], '15': [25, 26], '16': [27, 28], '17': [29], '18': [30, 31], '19': [32, 33], '20': [34], '21': [35, 36], '22': [37], '23': [38], '24': [39], '25': [40, 41], '26': [42, 43], '27': [44, 45], '28': [46, 47], '29': [48], '30': [49], '31': [50], '32': [51], '33': [52], '34': [53, 54], '35': [55], '36': [56], '37': [57], '38': [58], '39': [59], '40': [60], '41': [61], '42': [62], '43': [63], '44': [64]}


In [4]:
#DFe=configuraciones de cursos demandados por el estudiante e
#StudentId	CoursesList
dicc_DFe = {}
for index, col in df_students.iterrows():
    dicc_DFe[int(col["StudentId"])] = [int(x) for x in col["CoursesList"]]
print(dicc_DFe)

{1: [4], 2: [1], 3: [20, 26], 4: [5], 5: [21, 23], 6: [4], 7: [21, 23, 44], 8: [17], 9: [18], 10: [1], 11: [18, 24, 25], 12: [25], 13: [20], 14: [4, 9], 15: [1], 16: [23], 17: [14], 18: [14], 19: [18, 25], 20: [20, 24], 21: [16, 23], 22: [1], 23: [14], 24: [14], 25: [20, 23, 24], 26: [1], 27: [20, 24], 28: [1], 29: [3], 30: [3], 31: [14], 32: [21], 33: [1], 34: [1], 35: [4], 36: [1], 37: [1], 38: [3], 39: [20], 40: [1], 41: [20, 23], 42: [1], 43: [16], 44: [3], 45: [17], 46: [14], 47: [1], 48: [5, 10], 49: [3], 50: [20, 26], 51: [1], 52: [17], 53: [1], 54: [14], 55: [14], 56: [1], 57: [14], 58: [14], 59: [14], 60: [3], 61: [3], 62: [1], 63: [17], 64: [14], 65: [17], 66: [3], 67: [14], 68: [14], 69: [14], 70: [1], 71: [1], 72: [14], 73: [14], 74: [14], 75: [14], 76: [1], 77: [3], 78: [20], 79: [14], 80: [3], 81: [1], 82: [3], 83: [1], 84: [1], 85: [3], 86: [14], 87: [6], 88: [3], 89: [3], 90: [3], 91: [1], 92: [1], 93: [1], 94: [1], 95: [3], 96: [1], 97: [1], 98: [14], 99: [1], 100: [3]

In [5]:
#UTs=tiempo no disponible para la sala s
#RoomId	UnavailableDaysList	UnavailableStartList	UnavailableLengthList	UnavailableWeeksList
dicc_UTs = {}
for index, col in df_rooms.iterrows():
    if col["UnavailableDaysList"] != None:
        dicc_UTs[col["RoomId"]] = [col["UnavailableDaysList"],col["UnavailableStartList"],col["UnavailableLengthList"],col["UnavailableWeeksList"]]
print(dicc_UTs)

{'1': [['0010000'], ['222'], ['36'], ['111111111111111']], '11': [['1000000'], ['90'], ['132'], ['111111111111111']]}


In [81]:
## TDc=tiempos en los que se puede impartir la clase c
dicc_TDc = {}
for index,row in df_relation_class_time.iterrows():
    if int(row["ClassId"]) not in dicc_TDc.keys():
        dicc_TDc[int(row["ClassId"])] = [[row["TimeDays"],row["TimeStart"],row["TimeLength"],row["TimeWeeks"],row["TimePenalty"]]]
    else:
        dicc_TDc[int(row["ClassId"])].append([row["TimeDays"],row["TimeStart"],row["TimeLength"],row["TimeWeeks"],row["TimePenalty"]])

#for i in dicc_TDc:
    #print(i,dicc_TDc[i])

dicc_TDc2 = dicc_TDc
dicc_TDc = {}
contador = 0
for e,i in enumerate(dicc_TDc2):
    for j in dicc_TDc2[i]:
        if i not in dicc_TDc.keys():
            dicc_TDc[i] = []
        dicc_TDc[i].append(contador)
        contador+=1
#cont2 = 5000
#for i in dicc_TDc:
#    dicc_TDc[i].append(cont2)
#    cont2 += 1
#print(dicc_TDc)


In [7]:
dicc_t = {}
for index,row in df_relation_class_time.iterrows():
    dicc_t[index] = [row["ClassId"],row["TimeDays"],row["TimeStart"],row["TimeLength"],row["TimeWeeks"],row["TimePenalty"]]
print(dicc_t)

{0: ['1', '0100000', '90', 22, '111111111111111', '0'], 1: ['1', '0010000', '90', 22, '111111111111111', '0'], 2: ['1', '0001000', '90', 22, '111111111111111', '0'], 3: ['1', '0000100', '90', 22, '111111111111111', '0'], 4: ['1', '0100000', '114', 22, '111111111111111', '0'], 5: ['1', '0010000', '114', 22, '111111111111111', '0'], 6: ['1', '0001000', '114', 22, '111111111111111', '0'], 7: ['1', '0000100', '114', 22, '111111111111111', '0'], 8: ['1', '0100000', '138', 22, '111111111111111', '0'], 9: ['1', '0010000', '138', 22, '111111111111111', '0'], 10: ['1', '0001000', '138', 22, '111111111111111', '0'], 11: ['1', '0000100', '138', 22, '111111111111111', '0'], 12: ['1', '0100000', '162', 22, '111111111111111', '0'], 13: ['1', '0010000', '162', 22, '111111111111111', '0'], 14: ['1', '0001000', '162', 22, '111111111111111', '0'], 15: ['1', '0000100', '162', 22, '111111111111111', '0'], 16: ['1', '0100000', '186', 22, '111111111111111', '0'], 17: ['1', '0010000', '186', 22, '11111111111

In [8]:
## SDc=salas disponibles para la clase c

dicc_SDispc = {}
for index, row in df_relation_class_room.iterrows():
    if int(row["ClassId"]) not in dicc_SDispc.keys():
        dicc_SDispc[int(row["ClassId"])]=[int(row["RoomId"])]
    else:
        dicc_SDispc[int(row["ClassId"])].append(int(row["RoomId"]))

print(dicc_SDispc)

{1: [10, 11, 12], 2: [10, 11, 12], 3: [10, 11, 12], 4: [10, 11, 12], 5: [10, 11, 12], 6: [10, 11, 12], 7: [10, 11, 12], 8: [10, 11, 12], 9: [10, 11, 12], 10: [10, 11, 12], 11: [10, 11, 12], 12: [10, 11, 12], 13: [10, 11, 12], 14: [10, 11, 12], 15: [10, 11, 12], 16: [10, 11, 12], 17: [10, 11, 12], 18: [10, 11, 12], 19: [10, 11, 12], 20: [10, 11, 12], 21: [10, 11, 12], 22: [10, 11, 12], 23: [10, 11, 12], 24: [10, 11, 12], 25: [10, 11, 12], 26: [10, 11, 12], 27: [1], 28: [13], 29: [13], 30: [13], 31: [13], 32: [13], 33: [13], 34: [13], 35: [13], 36: [13], 37: [13], 38: [13], 39: [13], 40: [13], 41: [13], 42: [13], 43: [1, 2, 3], 44: [1, 2, 3], 45: [1, 2, 3], 46: [1, 2, 3], 47: [1, 2, 3], 48: [1, 2, 3], 49: [1, 2, 3], 50: [1, 2, 3], 51: [7], 52: [7], 53: [7], 54: [7], 55: [7], 56: [7], 57: [7], 58: [7], 59: [1, 2, 3], 60: [1, 2, 3], 61: [1, 2, 3], 62: [1, 2, 3], 63: [1, 2, 3], 64: [1, 2, 3], 65: [1, 2, 3], 66: [1, 2, 3], 67: [1, 2, 3], 68: [7], 69: [7], 70: [7], 71: [7], 72: [7], 73: [7], 

In [9]:
#SAc=clases c de la distribución same attendees
dicc_SAc = {}
for index, col in df_distributions.iterrows():
    if col["DistributionType"] == "SameAttendees":
        dicc_SAc[col["ClassesList"][0]] = [int(x) for x in col["ClassesList"]] 

print(dicc_SAc)
        

{'140': [140, 155, 156], '145': [145, 165], '28': [28, 27], '29': [29, 27], '51': [51, 43], '52': [52, 44], '53': [53, 45], '54': [54, 46], '55': [55, 47], '56': [56, 48], '57': [57, 49], '58': [58, 50], '68': [68, 59], '69': [69, 60], '70': [70, 61], '71': [71, 62], '72': [72, 63], '73': [73, 64], '74': [74, 65], '75': [75, 66], '76': [76, 67], '78': [78, 77], '79': [79, 77], '82': [82, 81], '84': [84, 83], '86': [86, 85], '89': [89, 87], '90': [90, 88], '93': [93, 91], '94': [94, 92], '96': [96, 95], '120': [120, 119], '121': [121, 119], '123': [123, 122], '124': [124, 122], '125': [125, 122], '130': [130, 129], '131': [131, 129], '132': [132, 129], '134': [134, 133], '135': [135, 133], '141': [141, 140], '142': [142, 140], '147': [147, 146], '148': [148, 146], '149': [149, 146], '151': [151, 150], '152': [152, 150], '153': [153, 154], '156': [156, 155], '163': [163, 162], '164': [164, 162]}


In [10]:
#SAc=clases c de la distribución same attendees
for index, col in df_distributions.iterrows():
    print(col["DistributionType"])


SameAttendees
SameAttendees
NotOverlap
NotOverlap
NotOverlap
NotOverlap
NotOverlap
NotOverlap
NotOverlap
NotOverlap
SameRoom
SameRoom
SameRoom
SameRoom
SameRoom
SameRoom
SameRoom
SameRoom
SameTime
SameTime
SameTime
SameTime
SameTime
SameTime
SameTime
SameTime
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
SameAttendees
NotOverlap
NotOverlap
NotOverlap
NotOver

In [11]:
#SSc =clases c de la distribución same start
dicc_SSc = {}
for index, col in df_distributions.iterrows():
    #print(col["DistributionType"])
    if col["DistributionType"] == "SameStart":
        dicc_SSc[col["ClassesList"][0]] = [int(x) for x in col["ClassesList"]] 
print(dicc_SSc)

{}


In [12]:
#STc =clases c de la distribución same time
dicc_STc = {}
for index, col in df_distributions.iterrows():
    #print(col["DistributionType"])
    if col["DistributionType"] == "SameTime":
        dicc_STc[col["ClassesList"][0]] = [int(x) for x in col["ClassesList"]] 
print(dicc_STc)

{'81': [81, 82, 63], '83': [83, 84, 48], '85': [85, 86, 64], '87': [87, 89, 49], '88': [88, 90, 50], '91': [91, 93, 65], '92': [92, 94, 66], '95': [95, 96, 67]}


In [13]:
#SRc =clases c de la distribución same room
dicc_SRc = {}
for index, col in df_distributions.iterrows():
    if col["DistributionType"] == "SameRoom":
        dicc_SRc[col["ClassesList"][0]] = [int(x) for x in col["ClassesList"]] 
#print(dicc_SRc)

dicc_SRc2 = {}
for e in range(len(df_classes)+1):
    for i in dicc_SRc:
        #print(i,e,dicc_SRc[i])
        if str(i) == str(e):
            dicc_SRc2[e] = dicc_SRc[i]
        if e not in dicc_SRc2.keys():
            dicc_SRc2[e] = []

#dicc_SRc = dicc_SRc2
print(dicc_SRc)
##{'81': [81, 82], '83': [83, 84], '85': [85, 86], '87': [87, 88], '89': [89, 90], '91': [91, 92], '93': [93, 94], '95': [95, 96]}

{'81': [81, 82], '83': [83, 84], '85': [85, 86], '87': [87, 88], '89': [89, 90], '91': [91, 92], '93': [93, 94], '95': [95, 96]}


In [14]:
## SDc=clases c de la distribución same days
dicc_SDc = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="SameDays":
        c1 = row["ClassesList"][0]
        #print(c1)
        dicc_SDc[c1] = []
        for i in range(len(row["ClassesList"])):
            dicc_SDc[c1].append(row["ClassesList"][i])
print(dicc_SDc)

{}


In [15]:
## PRc=clases c de la distribución precedence
dicc_PRc = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"]=="Precedence":
        c1 = row["ClassesList"][0]
        #print(c1)
        dicc_PRc[c1] = []
        for i in range(len(row["ClassesList"])):
            dicc_PRc[c1].append(row["ClassesList"][i])
print(dicc_PRc)

{}


In [16]:
#SPCc=id de la subparte a la que pertenece c
#dicc_subparts = {}
#dicc_SPCc = {}
#for index, row in df_subparts.iterrows():
#    dicc_subparts[row["SubpartId"]] = row["ClassIdList"]

#for subpartes in dicc_subparts:
#    for clases in dicc_subparts[subpartes]:
#        dicc_SPCc[clases] = int(subpartes)
#print(dicc_SPCc)

In [17]:
#Dc=duración de slots de clase c
dicc_Dc = {}
for index, row in df_relation_class_time.iterrows():
    dicc_Dc[row["ClassId"]] =  row["TimeLength"]
print(dicc_Dc)

{'1': 22, '2': 22, '3': 22, '4': 22, '5': 22, '6': 22, '7': 22, '8': 22, '9': 22, '10': 22, '11': 22, '12': 22, '13': 22, '14': 22, '15': 22, '16': 22, '17': 22, '18': 22, '19': 22, '20': 22, '21': 22, '22': 22, '23': 22, '24': 22, '25': 22, '26': 22, '27': 10, '28': 22, '29': 22, '30': 22, '31': 22, '32': 22, '33': 22, '34': 22, '35': 22, '36': 22, '37': 22, '38': 22, '39': 22, '40': 22, '41': 22, '42': 22, '43': 10, '44': 10, '45': 10, '46': 10, '47': 10, '48': 10, '49': 10, '50': 10, '51': 22, '52': 22, '53': 22, '54': 22, '55': 22, '56': 22, '57': 22, '58': 22, '59': 10, '60': 10, '61': 10, '62': 10, '63': 10, '64': 10, '65': 10, '66': 10, '67': 10, '68': 22, '69': 22, '70': 22, '71': 22, '72': 22, '73': 22, '74': 22, '75': 22, '76': 22, '77': 15, '78': 22, '79': 22, '80': 10, '81': 10, '82': 10, '83': 10, '84': 10, '85': 10, '86': 10, '87': 10, '88': 10, '89': 10, '90': 10, '91': 10, '92': 10, '93': 10, '94': 10, '95': 10, '96': 10, '97': 22, '98': 22, '99': 22, '100': 22, '101': 

In [18]:
#TSc=slot de inicio de la clase c
dicc_TSc = {}
for index, row in df_relation_class_time.iterrows():
    if row["ClassId"] not in dicc_TSc:
        dicc_TSc[row["ClassId"]] = []
    if row["TimeStart"] not in dicc_TSc[row["ClassId"]]:
        dicc_TSc[row["ClassId"]].append(row["TimeStart"])

for i in dicc_TSc:
    dicc_TSc[i] = [int(x) for x in dicc_TSc[i]]
print(dicc_TSc)
    

{'1': [90, 114, 138, 162, 186], '2': [90, 114, 138, 162, 186], '3': [90, 114, 138, 162, 186], '4': [90, 114, 138, 162, 186], '5': [90, 114, 138, 162, 186], '6': [90, 114, 138, 162, 186], '7': [90, 114, 138, 162, 186], '8': [90, 114, 138, 162, 186], '9': [90, 114, 138, 162, 186], '10': [90, 114, 138, 162, 186], '11': [90, 114, 138, 162, 186], '12': [90, 114, 138, 162, 186], '13': [90, 114, 138, 162, 186], '14': [90, 114, 138, 162, 186], '15': [90, 114, 138, 162, 186], '16': [90, 114, 138, 162, 186], '17': [90, 114, 138, 162, 186], '18': [90, 114, 138, 162, 186], '19': [90, 114, 138, 162, 186], '20': [90, 114, 138, 162, 186], '21': [90, 114, 138, 162, 186], '22': [90, 114, 138, 162, 186], '23': [90, 114, 138, 162, 186], '24': [90, 114, 138, 162, 186], '25': [90, 114, 138, 162, 186], '26': [90, 114, 138, 162, 186], '27': [90, 102, 114, 126, 138, 150, 162, 174, 186, 198], '28': [90, 114, 138, 162, 186], '29': [90, 114, 138, 162, 186], '30': [90, 114, 138, 162, 186], '31': [90, 114, 138, 16

In [19]:
## CPc=clase padre de la clase c
dicc_CPc = {}
for index,row in df_classes.iterrows():
    dicc_CPc[int(row["ClassId"])] = row["ClassParent"]
print(dicc_CPc)

{1: None, 2: None, 3: None, 4: None, 5: None, 6: None, 7: None, 8: None, 9: None, 10: None, 11: None, 12: None, 13: None, 14: None, 15: None, 16: None, 17: None, 18: None, 19: None, 20: None, 21: None, 22: None, 23: None, 24: None, 25: None, 26: None, 27: None, 28: None, 29: None, 30: None, 31: None, 32: None, 33: None, 34: None, 35: None, 36: None, 37: None, 38: None, 39: None, 40: None, 41: None, 42: None, 43: None, 44: None, 45: None, 46: None, 47: None, 48: None, 49: None, 50: None, 51: '43', 52: '44', 53: '45', 54: '46', 55: '47', 56: '48', 57: '49', 58: '50', 59: None, 60: None, 61: None, 62: None, 63: None, 64: None, 65: None, 66: None, 67: None, 68: '59', 69: '60', 70: '61', 71: '62', 72: '63', 73: '64', 74: '65', 75: '66', 76: '67', 77: None, 78: None, 79: None, 80: None, 81: None, 82: '81', 83: None, 84: '83', 85: None, 86: '85', 87: None, 88: None, 89: '87', 90: '88', 91: None, 92: None, 93: '91', 94: '92', 95: None, 96: '95', 97: None, 98: None, 99: None, 100: None, 101: No

In [20]:
## QSs=capacidad de estudiantes de la sala s 
dicc_QSs = {}
for index,row in df_rooms.iterrows():
    dicc_QSs[int(row["RoomId"])] = int(row["Capacity"])
print(dicc_QSs)

{1: 61, 2: 36, 3: 36, 4: 22, 5: 25, 6: 25, 7: 24, 8: 25, 9: 25, 10: 22, 11: 26, 12: 26, 13: 30}


In [21]:
## QCc=capacidad de estudiantes de la clase c
dicc_QCc = {}
for index,row in df_classes.iterrows():
    #if int(row["ClassId"]) not in dicc_QCc.keys():
        dicc_QCc[int(row["ClassId"])] = int(row["ClassLimit"])
print(dicc_QCc)

{1: 22, 2: 22, 3: 22, 4: 22, 5: 22, 6: 22, 7: 22, 8: 22, 9: 22, 10: 22, 11: 22, 12: 22, 13: 22, 14: 22, 15: 22, 16: 22, 17: 22, 18: 22, 19: 22, 20: 22, 21: 22, 22: 22, 23: 22, 24: 22, 25: 22, 26: 22, 27: 54, 28: 27, 29: 27, 30: 27, 31: 27, 32: 27, 33: 27, 34: 27, 35: 27, 36: 27, 37: 27, 38: 27, 39: 27, 40: 27, 41: 27, 42: 27, 43: 22, 44: 22, 45: 22, 46: 22, 47: 22, 48: 22, 49: 22, 50: 22, 51: 22, 52: 22, 53: 22, 54: 22, 55: 22, 56: 22, 57: 22, 58: 22, 59: 22, 60: 22, 61: 22, 62: 22, 63: 22, 64: 22, 65: 22, 66: 22, 67: 22, 68: 22, 69: 22, 70: 22, 71: 22, 72: 22, 73: 22, 74: 22, 75: 22, 76: 22, 77: 60, 78: 30, 79: 30, 80: 22, 81: 22, 82: 22, 83: 22, 84: 22, 85: 22, 86: 22, 87: 22, 88: 22, 89: 22, 90: 22, 91: 22, 92: 22, 93: 22, 94: 22, 95: 22, 96: 22, 97: 22, 98: 22, 99: 22, 100: 22, 101: 22, 102: 22, 103: 22, 104: 22, 105: 22, 106: 22, 107: 22, 108: 22, 109: 22, 110: 22, 111: 22, 112: 22, 113: 22, 114: 22, 115: 22, 116: 22, 117: 22, 118: 22, 119: 44, 120: 22, 121: 22, 122: 60, 123: 20, 

In [22]:
import math
#Agrupar capacidad de cursos

#print("Límite de las clases | Cantidad de clases con el límite")
#display(df_classes.groupby("ClassLimit").count()["ClassId"])

dicc_cursos = {}
#display(df_courses)
for index, row in df_courses.iterrows():
    dicc_cursos[row["CourseId"]] = row["ConfigIdList"]
#print(dicc_cursos)      
dicc_configs = {}
#display(df_configs)
for index, row in df_configs.iterrows():
    dicc_configs[row["ConfigId"]] = row["SubpartIdList"]
#print(dicc_configs)
dicc_subparts = {}
#display(df_subparts)
for index, row in df_subparts.iterrows():
    dicc_subparts[row["SubpartId"]] = row["ClassIdList"]
#print(dicc_subparts)
dicc_classes = {}
#display(df_classes)
for index, row in df_classes.iterrows():
    dicc_classes[row["ClassId"]] = row["ClassLimit"]
#print(dicc_classes)

dicc_lim = {}
dicc_curso_clase = {}
for p,i in dicc_cursos.items():
    for j in i:
        if j in dicc_configs.keys():
            #print(dicc_configs[j])
            for k in dicc_configs[j]:
                if k in dicc_subparts.keys():
                    #print(dicc_subparts[k])
                    for l in dicc_subparts[k]:
                        #print(l)
                        #Agregué estas lineas para hacerme un diccionario de curso con clase#
                        if l not in dicc_curso_clase:
                            dicc_curso_clase[l] = []
                        dicc_curso_clase[l].append(p)
                        ######################################################################
                        if l in dicc_classes.keys():
                            n = int(dicc_classes[l])
                            if p not in dicc_lim.keys():
                                dicc_lim[p] = [n]
                            else:
                                dicc_lim[p].append(n)
                        
#print(dicc_lim)
#print("Id de curso | Limite de alumnos")
for i in dicc_lim.keys():
    suma = 0
    contador = 0
    for j in dicc_lim[i]:
        suma += j
        contador += 1
    promedio = suma/contador
    dicc_lim[i] = int(math.ceil(promedio/10.0))*10
   #print(i, dicc_lim[i])
print(dicc_lim)

{'1': 30, '2': 40, '3': 30, '4': 30, '5': 30, '6': 40, '7': 30, '8': 30, '9': 30, '10': 30, '11': 30, '12': 30, '13': 30, '14': 30, '15': 30, '16': 30, '17': 30, '18': 20, '19': 30, '20': 30, '21': 30, '22': 40, '23': 60, '24': 30, '25': 30, '26': 30, '27': 20, '28': 20, '29': 40, '30': 40, '31': 50, '32': 40, '33': 30, '34': 30, '35': 40, '36': 30, '37': 40, '38': 20, '39': 20, '40': 30, '41': 20, '42': 20, '43': 20, '44': 40}


In [23]:
## cursos más demandados por estudiantes
dic_demanda_cursos = {}
for index,row in df_students.iterrows():
    for i in row["StudentId"]:
        for j in row["CoursesList"]:
            if j not in dic_demanda_cursos.keys():
                dic_demanda_cursos[j] = 1
                #print("agregado:",j,dic_demanda_cursos[j])
            else:
                dic_demanda_cursos[j] += 1
                #print("suma +1:",j,dic_demanda_cursos[j])
#print("Id Curso | Cantidad demandada")
for w in dic_demanda_cursos.keys():    
    print(w,dic_demanda_cursos[w])

4 499
1 1823
20 216
26 58
5 552
21 104
23 121
44 136
17 214
18 72
24 69
25 176
9 63
14 1582
16 178
3 1041
10 65
6 175
12 109
7 82
11 128
8 69
15 132
19 89
13 60
28 71
30 59
36 55
37 84
43 40
32 76
33 12
35 48
38 24


In [24]:
## Conteo de las salas mas utilizadas

dicc_conteo_clases_sala = {}
for index, row in df_relation_class_room.iterrows():
    if row["RoomId"] not in dicc_conteo_clases_sala.keys():
        dicc_conteo_clases_sala[row["RoomId"]] = 1
    else:
        dicc_conteo_clases_sala[row["RoomId"]] += 1
#print(dicc_conteo_clases_sala)
#print(len(dicc_conteo_clases_sala.keys()))
print("Sala | Cantidad de veces que se solicita")
#{k: v for k, v in sorted(dicc_conteo_clases_sala.items(), key=lambda item: item[1])}
#for i in sorted(dicc_conteo_clasess_sala)

Sala | Cantidad de veces que se solicita


In [25]:
## Dj=distribuciones de tipo j
dicc_Dj = {1:"Same Attendees",2:"Same Start",3:"Same Room",4:"Same Time",5:"Same Days",6:"Precedence"}

In [26]:
lista_I = []
for i in range(1,103):
    lista_I.append(i)
print(lista_I)

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102]


In [27]:
dicc_Ij = {1:[],2:[],3:[],4:[],5:[],6:[]}
for index, row in df_distributions.iterrows():
    if row["DistributionType"] == "SameAttendees":
        dicc_Ij[1].append(row["DistributionId"])
    elif row["DistributionType"] == "SameStart":
        dicc_Ij[2].append(row["DistributionId"])
    elif row["DistributionType"] == "SameRoom":
        dicc_Ij[3].append(row["DistributionId"])
    elif row["DistributionType"] == "SameTime":
        dicc_Ij[4].append(row["DistributionId"])
    elif row["DistributionType"] == "SameDays":
        dicc_Ij[5].append(row["DistributionId"])
    elif row["DistributionType"] == "Precedence":
        dicc_Ij[6].append(row["DistributionId"])
        
print(dicc_Ij)

{1: [1, 2, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76], 2: [], 3: [11, 12, 13, 14, 15, 16, 17, 18], 4: [19, 20, 21, 22, 23, 24, 25, 26], 5: [], 6: []}


In [82]:
dicc_PTct = {}
for index, row in df_relation_class_time.iterrows():
    llave = (int(row["ClassId"]),int(index))
    dicc_PTct[llave] = int(row["TimePenalty"]) 

#dicc_PTct2 = dicc_PTct.copy()
#contador = 5000
#for i in dicc_PTct2:
#    llave = (i[0],contador)
#    dicc_PTct[llave] = 9999
#    contador += 1
print(dicc_PTct)

{(1, 0): 0, (1, 1): 0, (1, 2): 0, (1, 3): 0, (1, 4): 0, (1, 5): 0, (1, 6): 0, (1, 7): 0, (1, 8): 0, (1, 9): 0, (1, 10): 0, (1, 11): 0, (1, 12): 0, (1, 13): 0, (1, 14): 0, (1, 15): 0, (1, 16): 0, (1, 17): 0, (1, 18): 0, (1, 19): 0, (2, 20): 0, (2, 21): 0, (2, 22): 0, (2, 23): 0, (2, 24): 0, (2, 25): 0, (2, 26): 0, (2, 27): 0, (2, 28): 0, (2, 29): 0, (2, 30): 0, (2, 31): 0, (2, 32): 0, (2, 33): 0, (2, 34): 0, (2, 35): 0, (2, 36): 0, (2, 37): 0, (2, 38): 0, (2, 39): 0, (3, 40): 0, (3, 41): 0, (3, 42): 0, (3, 43): 0, (3, 44): 0, (3, 45): 0, (3, 46): 0, (3, 47): 0, (3, 48): 0, (3, 49): 0, (3, 50): 0, (3, 51): 0, (3, 52): 0, (3, 53): 0, (3, 54): 0, (3, 55): 0, (3, 56): 0, (3, 57): 0, (3, 58): 0, (3, 59): 0, (4, 60): 0, (4, 61): 0, (4, 62): 0, (4, 63): 0, (4, 64): 0, (4, 65): 0, (4, 66): 0, (4, 67): 0, (4, 68): 0, (4, 69): 0, (4, 70): 0, (4, 71): 0, (4, 72): 0, (4, 73): 0, (4, 74): 0, (4, 75): 0, (4, 76): 0, (4, 77): 0, (4, 78): 0, (4, 79): 0, (5, 80): 0, (5, 81): 0, (5, 82): 0, (5, 83): 0, (

In [29]:
dicc_PScs = {}
for index, row in df_relation_class_room.iterrows():
    llave = (int(row["ClassId"]),int(row["RoomId"]))
    dicc_PScs[llave] = int(row["RoomPenalty"]) 
print(dicc_PScs)

{(1, 10): 0, (1, 11): 0, (1, 12): 0, (2, 10): 0, (2, 11): 0, (2, 12): 0, (3, 10): 0, (3, 11): 0, (3, 12): 0, (4, 10): 0, (4, 11): 0, (4, 12): 0, (5, 10): 0, (5, 11): 0, (5, 12): 0, (6, 10): 0, (6, 11): 0, (6, 12): 0, (7, 10): 0, (7, 11): 0, (7, 12): 0, (8, 10): 0, (8, 11): 0, (8, 12): 0, (9, 10): 0, (9, 11): 0, (9, 12): 0, (10, 10): 0, (10, 11): 0, (10, 12): 0, (11, 10): 0, (11, 11): 0, (11, 12): 0, (12, 10): 0, (12, 11): 0, (12, 12): 0, (13, 10): 0, (13, 11): 0, (13, 12): 0, (14, 10): 0, (14, 11): 0, (14, 12): 0, (15, 10): 0, (15, 11): 0, (15, 12): 0, (16, 10): 0, (16, 11): 0, (16, 12): 0, (17, 10): 0, (17, 11): 0, (17, 12): 0, (18, 10): 0, (18, 11): 0, (18, 12): 0, (19, 10): 0, (19, 11): 0, (19, 12): 0, (20, 10): 0, (20, 11): 0, (20, 12): 0, (21, 10): 0, (21, 11): 0, (21, 12): 0, (22, 10): 0, (22, 11): 0, (22, 12): 0, (23, 10): 0, (23, 11): 0, (23, 12): 0, (24, 10): 0, (24, 11): 0, (24, 12): 0, (25, 10): 0, (25, 11): 0, (25, 12): 0, (26, 10): 0, (26, 11): 0, (26, 12): 0, (27, 1): 0, 

In [30]:
##################### GUROBI #######################

In [31]:
from gurobipy import *
from random   import *
import numpy as np
import gurobipy as gp
from gurobipy import GRB

In [32]:
dicc_clases = {}
dicc_salas = {}
dicc_estudiantes = {}
dicc_tiempos = {}
dicc_combinaciones = {}
for e, clase in enumerate(dicc_classes):
    dicc_clases[e+1]= clase

for index, estudiante in df_students.iterrows():
    dicc_estudiantes[index+1] = estudiante["StudentId"]

for index, sala in df_rooms.iterrows():
    dicc_salas[index+1] = sala["RoomId"]

c = 0
for clase in dicc_TDc:
    for tiempo in dicc_TDc[clase]:
        if tiempo not in dicc_tiempos.values():
            dicc_tiempos[c] = tiempo
            c += 1

dicc_classes_times = {}
for index, row in df_relation_class_time.iterrows():
    if row["ClassId"] not in dicc_classes_times.keys():
        dicc_classes_times[row["ClassId"]] = []
    lista = [row["TimeDays"],row["TimeStart"],row["TimeLength"],row["TimeWeeks"],row["TimePenalty"]]
    dicc_classes_times[row["ClassId"]].append(lista)
    lista = []

dicc_configuraciones = {}
for index,row in df_configs.iterrows():
    dicc_configuraciones[int(row["ConfigId"])] = row["SubpartIdList"]
print(dicc_configuraciones)

{1: ['1'], 2: ['2', '3'], 3: ['4'], 4: ['5', '6'], 5: ['7', '8'], 6: ['9', '10'], 7: ['11'], 8: ['12', '13'], 9: ['14', '15'], 10: ['16', '17'], 11: ['18', '19'], 12: ['20', '21'], 13: ['22', '23'], 14: ['24'], 15: ['25', '26'], 16: ['27', '28'], 17: ['29'], 18: ['30', '31'], 19: ['32', '33'], 20: ['34'], 21: ['35', '36'], 22: ['37'], 23: ['38'], 24: ['39'], 25: ['40', '41'], 26: ['42', '43'], 27: ['44', '45'], 28: ['46', '47'], 29: ['48'], 30: ['49'], 31: ['50'], 32: ['51'], 33: ['52'], 34: ['53', '54'], 35: ['55'], 36: ['56'], 37: ['57'], 38: ['58'], 39: ['59'], 40: ['60'], 41: ['61'], 42: ['62'], 43: ['63'], 44: ['64']}


In [33]:
c = 0
dicc_tiempos2 = {}
for clase in dicc_TDc2:
    for tiempo in dicc_TDc2[clase]:
        if tiempo not in dicc_tiempos2.values():
            dicc_tiempos2[c] = tiempo
            c += 1
print(dicc_tiempos2)

{0: ['0100000', '90', 22, '111111111111111', '0'], 1: ['0010000', '90', 22, '111111111111111', '0'], 2: ['0001000', '90', 22, '111111111111111', '0'], 3: ['0000100', '90', 22, '111111111111111', '0'], 4: ['0100000', '114', 22, '111111111111111', '0'], 5: ['0010000', '114', 22, '111111111111111', '0'], 6: ['0001000', '114', 22, '111111111111111', '0'], 7: ['0000100', '114', 22, '111111111111111', '0'], 8: ['0100000', '138', 22, '111111111111111', '0'], 9: ['0010000', '138', 22, '111111111111111', '0'], 10: ['0001000', '138', 22, '111111111111111', '0'], 11: ['0000100', '138', 22, '111111111111111', '0'], 12: ['0100000', '162', 22, '111111111111111', '0'], 13: ['0010000', '162', 22, '111111111111111', '0'], 14: ['0001000', '162', 22, '111111111111111', '0'], 15: ['0000100', '162', 22, '111111111111111', '0'], 16: ['0100000', '186', 22, '111111111111111', '0'], 17: ['0010000', '186', 22, '111111111111111', '0'], 18: ['0001000', '186', 22, '111111111111111', '0'], 19: ['0000100', '186', 22

In [41]:
## De Cantidad de cursos pedidos por estudiante E
dicc_De = {}
for index,row in df_students.iterrows():
    dicc_De[int(row["StudentId"])] = len(row["CoursesList"])
print(dicc_De)

{1: 1, 2: 1, 3: 2, 4: 1, 5: 2, 6: 1, 7: 3, 8: 1, 9: 1, 10: 1, 11: 3, 12: 1, 13: 1, 14: 2, 15: 1, 16: 1, 17: 1, 18: 1, 19: 2, 20: 2, 21: 2, 22: 1, 23: 1, 24: 1, 25: 3, 26: 1, 27: 2, 28: 1, 29: 1, 30: 1, 31: 1, 32: 1, 33: 1, 34: 1, 35: 1, 36: 1, 37: 1, 38: 1, 39: 1, 40: 1, 41: 2, 42: 1, 43: 1, 44: 1, 45: 1, 46: 1, 47: 1, 48: 2, 49: 1, 50: 2, 51: 1, 52: 1, 53: 1, 54: 1, 55: 1, 56: 1, 57: 1, 58: 1, 59: 1, 60: 1, 61: 1, 62: 1, 63: 1, 64: 1, 65: 1, 66: 1, 67: 1, 68: 1, 69: 1, 70: 1, 71: 1, 72: 1, 73: 1, 74: 1, 75: 1, 76: 1, 77: 1, 78: 1, 79: 1, 80: 1, 81: 1, 82: 1, 83: 1, 84: 1, 85: 1, 86: 1, 87: 1, 88: 1, 89: 1, 90: 1, 91: 1, 92: 1, 93: 1, 94: 1, 95: 1, 96: 1, 97: 1, 98: 1, 99: 1, 100: 1, 101: 1, 102: 1, 103: 1, 104: 1, 105: 1, 106: 1, 107: 1, 108: 1, 109: 1, 110: 1, 111: 1, 112: 1, 113: 1, 114: 1, 115: 1, 116: 1, 117: 2, 118: 1, 119: 3, 120: 1, 121: 1, 122: 1, 123: 1, 124: 1, 125: 1, 126: 2, 127: 1, 128: 1, 129: 2, 130: 1, 131: 2, 132: 1, 133: 1, 134: 1, 135: 1, 136: 1, 137: 1, 138: 1, 139

In [54]:
dicc_PD1i = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"] == "SameAttendees":
        if row["DistributionPenalty"] is None:
            dp = 0
        else:
            dp = row["DistributionPenalty"]
        dicc_PD1i[row["DistributionId"]] = dp
        
dicc_PD4i = {}
for index,row in df_distributions.iterrows():
    if row["DistributionType"] == "SameTime":
        if row["DistributionPenalty"] is None:
            dp = 0
        else:
            dp = row["DistributionPenalty"]
        dicc_PD4i[row["DistributionId"]] = dp
print(dicc_PD1i)

{1: 0, 2: 0, 27: 0, 28: 0, 29: 0, 30: 0, 31: 0, 32: 0, 33: 0, 34: 0, 35: 0, 36: 0, 37: 0, 38: 0, 39: 0, 40: 0, 41: 0, 42: 0, 43: 0, 44: 0, 45: 0, 46: 0, 47: 0, 48: 0, 49: 0, 50: 0, 51: 0, 52: 0, 53: 0, 54: 0, 55: 0, 56: 0, 57: 0, 58: 0, 59: 0, 60: 0, 61: 0, 62: 0, 63: 0, 64: 0, 65: 0, 66: 0, 67: 0, 68: 0, 69: 0, 70: 0, 71: 0, 72: 0, 73: 0, 74: 0, 75: 0, 76: 0}


In [71]:
## Cursos pedidos por estudiante E
dicc_Ce = {}
#for index,row in df_students.iterrows():
 #       dicc_Ce[int(row["StudentId"])] = row["CoursesList"]
#print(dicc_Ce)

for index,row in df_students.iterrows():
    dicc_Ce[int(row["StudentId"])] = []
    for i in row["CoursesList"]:
        dicc_Ce[int(row["StudentId"])].append(int(i))
        #print(i)
#print(dicc_Ce)

#Cantidad de subpartes de una configuración
dicc_CS = {}
for index, col in df_configs.iterrows():
    dicc_CS[int(col["ConfigId"])] = len(col["SubpartIdList"])
#print(dicc_CS)

#Cantidad de subpartes que pide un estudiante E
dicc_Se = {}
for i in dicc_Ce.keys():
    dicc_Se[i]=0
    for j in dicc_Ce[i]:
       
        cant = dicc_CS[j]
        dicc_Se[i]+= cant
        #print(j)
#print(dicc_Se)

In [ ]:
timetabling = gp.Model("Asignacion de cursos a horarios y salas")

#Conjuntos
C = dicc_clases.keys()
F = dicc_configuraciones.keys()
S = dicc_salas.keys()
T = dicc_tiempos.keys()
E = dicc_estudiantes.keys()
I = lista_I

#subconjuntos
SDisp_c = dicc_SDispc
TD_c = dicc_TDc
DF_e = dicc_DFe
UT_s = dicc_UTs
SPF_f = dicc_SPFf
SA_c = dicc_SAc 
SS_c = dicc_SSc
SR_c = dicc_SRc
PR_c = dicc_PRc
SD_c = dicc_SDc
D_j = dicc_Dj
I_j = dicc_Ij
ST_c = dicc_STc
De = dicc_De
Se = dicc_Se

#parámetros
CP_c = dicc_CPc
QC_c = dicc_QCc
QS_s = dicc_QSs
D_c = dicc_Dc
TS_c = dicc_TSc
PS_cs = dicc_PScs
PT_ct = dicc_PTct
PD_1i = dicc_PD1i
#PD_2i
#PD_3i
PD_4i = dicc_PD4i
#PD_5i
#PD_6i
#PE_
alfa = int(df_optimization["Time"])
beta = int(df_optimization["Room"])
gamma = int(df_optimization["Distribution"])
delta = int(df_optimization["Student"])



x = {} 
for c in dicc_clases.keys():
    for t in dicc_tiempos.keys():
        x[c,t] = timetabling.addVar(vtype=gp.GRB.BINARY, name='x_'+str(c)+','+str(t))

y = {}
for c in dicc_clases.keys():
    for s in dicc_salas.keys():
        y[c,s] = timetabling.addVar(vtype=gp.GRB.BINARY, name='y_'+str(c)+','+str(s))

z = {}
for e in dicc_estudiantes.keys():
    for c in dicc_clases.keys():
        z[e,c] = timetabling.addVar(vtype=gp.GRB.BINARY, name='z_'+str(e)+','+str(c))

w = {}
for e in dicc_estudiantes.keys():
    for f in dicc_configuraciones.keys():
        w[e,f] = timetabling.addVar(vtype=gp.GRB.BINARY, name='w_'+str(e)+','+str(f))
        
xs = {}
for c in dicc_clases.keys():
    for t in dicc_tiempos.keys():
        xs[c,t] = timetabling.addVar(vtype=gp.GRB.BINARY, name='xs_'+str(c)+','+str(t))
        
aux = {}
for j in D_j.keys():
    for i in I:
        aux[j,i] = timetabling.addVar(vtype=gp.GRB.BINARY, name="aux_"+str(j)+","+str(i))


        
#Función Objetivo
timetabling.setObjective(alfa*gp.quicksum(x[c,t]*PT_ct[(c,t)] for c in C for t in TD_c[c])+beta*gp.quicksum(y[c,s]*PS_cs[(c,s)] for c in C for s in SDisp_c[c])+gamma*gp.quicksum(aux[1,i]*PD_1i[i] for i in I_j[1])+gamma*gp.quicksum(aux[4,i]*PD_4i[i] for i in I_j[4]),GRB.MINIMIZE)

#Restricciones
#A cada clase se le debe ser asignado un tiempo
timetabling.addConstrs(((gp.quicksum(x[c,t] for t in TD_c[c]) >= 1) for c in C), name = "R1")
#Cada clase debe ser asignada a una sala (donde sea aplicable)
timetabling.addConstrs(((gp.quicksum(y[c,s] for s in SDisp_c[c]) == 1) for c in C), name = "R2")
#Cada estudiante debe ser asignado a una configuración de curso para cada curso que demanda
timetabling.addConstrs(((w[e,f] == 1) for e in E for f in DF_e[e]), name = "R3")
timetabling.addConstrs(((gp.quicksum(w[e,f] for f in DF_e[e]) == De[e]) for e in E), name = "R3")
#Cada estudiante debe ser asignado a todas las clases que requiere
timetabling.addConstrs(((gp.quicksum(z[e,c] for c in C) == Se[e]) for e in E), name = "E")
#La capacidad de cada clase en términos del número de estudiantes debe ser satisfecha
timetabling.addConstrs(((gp.quicksum(z[e,c] for e in E) <= QC_c[c]*x[c,t]) for c in C for t in TD_c[c]), name = "R4")
#Una sala no puede ser usada cuando no está disponible
#timetabling.addConstrs(((y[c,s] + x[c,t] <= 1) for c in C for s in SDisp_c[c] for t in UT_s[s]), name = "R5")
#Dos clases no pueden ser asignadas en un mismo tiempo en la misma sala
timetabling.addConstrs(((x[c1,t1] + y[c1,s1] + x[c1,t2] + y[c2,s2] <= 3) for c1 in C for c2 in C for t1 in TD_c[c1] for t2 in TD_c[c2] for s1 in SDisp_c[c1] for s2 in SDisp_c[c2] if c1 != c2 if t1 == t2 if s1 == s2), name = "R6")
#SAME ATTENDEES
timetabling.addConstrs(((x[c1,t1] + x[c2,t2] == 2) for c1 in C for c2 in C for t1 in TD_c[c1] for t2 in TD_c[c2] if c1!=c2 if t1==t2 if c1 in SA_c[c2] or c2 in SA_c[c1]), name = "R7")
#SAME START
#timetabling.addConstrs(((xs[c1,t1] + xs[c2,t2] == 2) for c1 in C for c2 in C for t1 in TD_c[c1] for t2 in TD_c[c2] if c1 != c2 if dicc_tiempos2[t1][1]==dicc_tiempos2[t2][1] if c1 in SS_c[c2] or c2 in SS_c[c1]), name = "R8")
#SAME ROOMS
#timetabling.addConstrs(((y[c1,s1] + y[c2,s2] == 2) for c1 in C for c2 in C for s1 in SDisp_c[c1] for s2 in SDisp_c[c2] if c1!=c2 if s1==s2 if c1 in SR_c[c2] or c2 in SR_c[c1]), name = "R9")
#SAME TIME
timetabling.addConstrs(((x[c1,t1] + x[c2,t2] == 2) for c1 in C for c2 in C for t1 in TD_c[c1] for t2 in TD_c[c2] if c1!=c2 if t1==t2 if c1 in ST_c[c2] or c2 in ST_c[c1]), name = "R10")
#SAME DAYS
#timetabling.addConstrs(((xs[c1,t1] <= gp.quicksum(xs[c2,t2] for t2 in TD_c[c2])) for c1 in C for c2 in C for t1 in TD_c[c1] if c1!=c2 if dicc_tiempos2[t1][0]==dicc_tiempos2[t2][0] if c1 in SD_c[c2] or c2 in SD_c[c1]), name = "R11")
#timetabling.addConstrs(((xs[c1,t1] == xs[c2,t2+D_c[c2]+1]) for c1 in PR_c[c1] for c2 in PR_c[c2] for t1 in TD_c[c1] for t2 in TD_c[c2] if c1!=c2), name = "R13")


#Restricciones blandas
timetabling.addConstrs((((x[c1,t1] - x[c2,t2])*(x[c1,t1] - x[c2,t2]) == aux[1,i]*aux[1,i]) for c1 in C for c2 in C for t1 in TD_c[c1] for t2 in TD_c[c2] if c1 != c2 if t1 == t2 if c1 in SA_c[c2] or c2 in SA_c[c1]), name = "SameAttendees B")

#timetabling.addConstrs((xs[c1,t1]+xs[c2,t2]-2 == Aux[2,i] for c1 in SS_c[c1] for c2 in SS_c[c2] for t1 in TD_c[c1] for t2 in TD_c[c2] if c1 != c2 if dicc_tiempos2[t1][1]==dicc_tiempos2[t2][1]), name = "Same Start B")

#timetabling.addConstrs((y[c1,s1]+y[c2,s2]-2 == Aux[3,i] for c1 in SR_c[c1] for c2 in SR_c[c2] for s1 in SDisp_c[c1] for s2 in SDisp_c[c2] if c1 != c2 if s1 == s2), name = "Same Rooms B")

timetabling.addConstrs((((x[c1,t1] - x[c2,t2])*(x[c1,t1] - x[c2,t2]) == aux[4,i]*aux[4,i]) for c1 in C for c2 in C for t1 in TD_c[c1] for t2 in TD_c[c2] if c1!=c2 if t1==t2 if c1 in ST_c[c2] or c2 in ST_c[c1]), name = "Same Time B")

#timetabling.addConstrs((xs[c1,t1]-gp.quicksum(xs[c2,t2] for t2 in TD_c[c2]) <= Aux5 for c1 in SD_c[c1] for c2 in SD_c[c2] for t1 in TD_c[c1] if c1!=c2 if dicc_tiempos2[t1][0]==dicc_tiempos2[t2][0]), name = "Same Days B")

#timetabling.addConstrs((xs[c1,t1]-xs[c2,t1+dc+1] == Aux8[8,i] for c1 in PR_c[c1] for c2 in PR_c[c2] for t1 in TD_c[c1] if c1!=c2), name = "Precedence B")

## Relación entre variables

timetabling.addConstrs((x[c,t1] <= xs[c,t2] for c in C for t1 in TD_c[c] for t2 in TD_c[c] if t1 == t2), name ="RelacionX-XSn1")

timetabling.addConstrs(((xs[c,t] <= gp.quicksum(x[c,t] for t in TD_c[c])) for c in C), name = "RelacionX-XSn2")

#timetabling.addConstrs(((x[c,t] == y[c,s]) for c in C for t in TD_c[c] for s in SDisp_c[c]), name = "RelacionXS-Y")
timetabling.addConstrs(((quicksum(z[e,c] for c in C) >= quicksum(w[e,f] for f in F)) for e in E), name = "RelacionZ-W")


timetabling.optimize()
for v in timetabling.getVars():
    print('%s %g' % (v.varName, v.x))


Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 14837 rows, 1468694 columns and 6726840 nonzeros
Model fingerprint: 0x33c684df
Variable types: 0 continuous, 1468694 integer (1468694 binary)
Coefficient statistics:
  Matrix range     [1e+00, 6e+01]
  Objective range  [2e+00, 6e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 6e+00]
Found heuristic solution: objective 8736.0000000
Presolve removed 12661 rows and 1120307 columns
Presolve time: 4.82s
Presolved: 2176 rows, 348387 columns, 696735 nonzeros
Found heuristic solution: objective 7548.0000000
Variable types: 0 continuous, 348387 integer (348387 binary)

Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   3.141000e+03   0.000000e+00      6s
    4925    2.7222222e+02   0.000000e+00   0.000000e+00      8s

Root relaxation: objective 2.722222e+02, 4925 iterations, 1.91 seconds

    Nodes    |    Current Node    |     Objective Bo

x_1,1169 0
x_1,1170 0
x_1,1171 0
x_1,1172 0
x_1,1173 0
x_1,1174 0
x_1,1175 0
x_1,1176 0
x_1,1177 0
x_1,1178 0
x_1,1179 0
x_1,1180 0
x_1,1181 0
x_1,1182 0
x_1,1183 0
x_1,1184 0
x_1,1185 0
x_1,1186 0
x_1,1187 0
x_1,1188 0
x_1,1189 0
x_1,1190 0
x_1,1191 0
x_1,1192 0
x_1,1193 0
x_1,1194 0
x_1,1195 0
x_1,1196 0
x_1,1197 0
x_1,1198 0
x_1,1199 0
x_1,1200 0
x_1,1201 0
x_1,1202 0
x_1,1203 0
x_1,1204 0
x_1,1205 0
x_1,1206 0
x_1,1207 0
x_1,1208 0
x_1,1209 0
x_1,1210 0
x_1,1211 0
x_1,1212 0
x_1,1213 0
x_1,1214 0
x_1,1215 0
x_1,1216 0
x_1,1217 0
x_1,1218 0
x_1,1219 0
x_1,1220 0
x_1,1221 0
x_1,1222 0
x_1,1223 0
x_1,1224 0
x_1,1225 0
x_1,1226 0
x_1,1227 0
x_1,1228 0
x_1,1229 0
x_1,1230 0
x_1,1231 0
x_1,1232 0
x_1,1233 0
x_1,1234 0
x_1,1235 0
x_1,1236 0
x_1,1237 0
x_1,1238 0
x_1,1239 0
x_1,1240 0
x_1,1241 0
x_1,1242 0
x_1,1243 0
x_1,1244 0
x_1,1245 0
x_1,1246 0
x_1,1247 0
x_1,1248 0
x_1,1249 0
x_1,1250 0
x_1,1251 0
x_1,1252 0
x_1,1253 0
x_1,1254 0
x_1,1255 0
x_1,1256 0
x_1,1257 0
x_1,1258 0
x_1,1259 0

x_1,2719 0
x_1,2720 0
x_1,2721 0
x_1,2722 0
x_1,2723 0
x_1,2724 0
x_1,2725 0
x_1,2726 0
x_1,2727 0
x_1,2728 0
x_1,2729 0
x_1,2730 0
x_1,2731 0
x_1,2732 0
x_1,2733 0
x_1,2734 0
x_1,2735 0
x_1,2736 0
x_1,2737 0
x_1,2738 0
x_1,2739 0
x_1,2740 0
x_1,2741 0
x_1,2742 0
x_1,2743 0
x_1,2744 0
x_1,2745 0
x_1,2746 0
x_1,2747 0
x_1,2748 0
x_1,2749 0
x_1,2750 0
x_1,2751 0
x_1,2752 0
x_1,2753 0
x_1,2754 0
x_1,2755 0
x_1,2756 0
x_1,2757 0
x_1,2758 0
x_1,2759 0
x_1,2760 0
x_1,2761 0
x_1,2762 0
x_1,2763 0
x_1,2764 0
x_1,2765 0
x_1,2766 0
x_1,2767 0
x_1,2768 0
x_1,2769 0
x_1,2770 0
x_1,2771 0
x_1,2772 0
x_1,2773 0
x_1,2774 0
x_1,2775 0
x_1,2776 0
x_1,2777 0
x_1,2778 0
x_1,2779 0
x_1,2780 0
x_1,2781 0
x_1,2782 0
x_1,2783 0
x_1,2784 0
x_1,2785 0
x_1,2786 0
x_1,2787 0
x_1,2788 0
x_1,2789 0
x_1,2790 0
x_1,2791 0
x_1,2792 0
x_1,2793 0
x_1,2794 0
x_1,2795 0
x_1,2796 0
x_1,2797 0
x_1,2798 0
x_1,2799 0
x_1,2800 0
x_1,2801 0
x_1,2802 0
x_1,2803 0
x_1,2804 0
x_1,2805 0
x_1,2806 0
x_1,2807 0
x_1,2808 0
x_1,2809 0

x_2,648 0
x_2,649 0
x_2,650 0
x_2,651 0
x_2,652 0
x_2,653 0
x_2,654 0
x_2,655 0
x_2,656 0
x_2,657 0
x_2,658 0
x_2,659 0
x_2,660 0
x_2,661 0
x_2,662 0
x_2,663 0
x_2,664 0
x_2,665 0
x_2,666 0
x_2,667 0
x_2,668 0
x_2,669 0
x_2,670 0
x_2,671 0
x_2,672 0
x_2,673 0
x_2,674 0
x_2,675 0
x_2,676 0
x_2,677 0
x_2,678 0
x_2,679 0
x_2,680 0
x_2,681 0
x_2,682 0
x_2,683 0
x_2,684 0
x_2,685 0
x_2,686 0
x_2,687 0
x_2,688 0
x_2,689 0
x_2,690 0
x_2,691 0
x_2,692 0
x_2,693 0
x_2,694 0
x_2,695 0
x_2,696 0
x_2,697 0
x_2,698 0
x_2,699 0
x_2,700 0
x_2,701 0
x_2,702 0
x_2,703 0
x_2,704 0
x_2,705 0
x_2,706 0
x_2,707 0
x_2,708 0
x_2,709 0
x_2,710 0
x_2,711 0
x_2,712 0
x_2,713 0
x_2,714 0
x_2,715 0
x_2,716 0
x_2,717 0
x_2,718 0
x_2,719 0
x_2,720 0
x_2,721 0
x_2,722 0
x_2,723 0
x_2,724 0
x_2,725 0
x_2,726 0
x_2,727 0
x_2,728 0
x_2,729 0
x_2,730 0
x_2,731 0
x_2,732 0
x_2,733 0
x_2,734 0
x_2,735 0
x_2,736 0
x_2,737 0
x_2,738 0
x_2,739 0
x_2,740 0
x_2,741 0
x_2,742 0
x_2,743 0
x_2,744 0
x_2,745 0
x_2,746 0
x_2,747 0


x_2,1820 0
x_2,1821 0
x_2,1822 0
x_2,1823 0
x_2,1824 0
x_2,1825 0
x_2,1826 0
x_2,1827 0
x_2,1828 0
x_2,1829 0
x_2,1830 0
x_2,1831 0
x_2,1832 0
x_2,1833 0
x_2,1834 0
x_2,1835 0
x_2,1836 0
x_2,1837 0
x_2,1838 0
x_2,1839 0
x_2,1840 0
x_2,1841 0
x_2,1842 0
x_2,1843 0
x_2,1844 0
x_2,1845 0
x_2,1846 0
x_2,1847 0
x_2,1848 0
x_2,1849 0
x_2,1850 0
x_2,1851 0
x_2,1852 0
x_2,1853 0
x_2,1854 0
x_2,1855 0
x_2,1856 0
x_2,1857 0
x_2,1858 0
x_2,1859 0
x_2,1860 0
x_2,1861 0
x_2,1862 0
x_2,1863 0
x_2,1864 0
x_2,1865 0
x_2,1866 0
x_2,1867 0
x_2,1868 0
x_2,1869 0
x_2,1870 0
x_2,1871 0
x_2,1872 0
x_2,1873 0
x_2,1874 0
x_2,1875 0
x_2,1876 0
x_2,1877 0
x_2,1878 0
x_2,1879 0
x_2,1880 0
x_2,1881 0
x_2,1882 0
x_2,1883 0
x_2,1884 0
x_2,1885 0
x_2,1886 0
x_2,1887 0
x_2,1888 0
x_2,1889 0
x_2,1890 0
x_2,1891 0
x_2,1892 0
x_2,1893 0
x_2,1894 0
x_2,1895 0
x_2,1896 0
x_2,1897 0
x_2,1898 0
x_2,1899 0
x_2,1900 0
x_2,1901 0
x_2,1902 0
x_2,1903 0
x_2,1904 0
x_2,1905 0
x_2,1906 0
x_2,1907 0
x_2,1908 0
x_2,1909 0
x_2,1910 0

...

x_80,1203 0
x_80,1204 0
x_80,1205 0
x_80,1206 0
x_80,1207 0
x_80,1208 0
x_80,1209 0
x_80,1210 0
x_80,1211 0
x_80,1212 0
x_80,1213 0
x_80,1214 0
x_80,1215 0
x_80,1216 0
x_80,1217 0
x_80,1218 0
x_80,1219 0
x_80,1220 0
x_80,1221 0
x_80,1222 0
x_80,1223 0
x_80,1224 0
x_80,1225 0
x_80,1226 0
x_80,1227 0
x_80,1228 0
x_80,1229 0
x_80,1230 0
x_80,1231 0
x_80,1232 0
x_80,1233 0
x_80,1234 0
x_80,1235 0
x_80,1236 0
x_80,1237 0
x_80,1238 0
x_80,1239 0
x_80,1240 0
x_80,1241 0
x_80,1242 0
x_80,1243 0
x_80,1244 0
x_80,1245 0
x_80,1246 0
x_80,1247 0
x_80,1248 0
x_80,1249 0
x_80,1250 0
x_80,1251 0
x_80,1252 0
x_80,1253 0
x_80,1254 0
x_80,1255 0
x_80,1256 0
x_80,1257 0
x_80,1258 0
x_80,1259 0
x_80,1260 0
x_80,1261 0
x_80,1262 0
x_80,1263 0
x_80,1264 0
x_80,1265 0
x_80,1266 0
x_80,1267 0
x_80,1268 0
x_80,1269 0
x_80,1270 0
x_80,1271 0
x_80,1272 0
x_80,1273 0
x_80,1274 0
x_80,1275 0
x_80,1276 0
x_80,1277 0
x_80,1278 0
x_80,1279 0
x_80,1280 0
x_80,1281 0
x_80,1282 0
x_80,1283 0
x_80,1284 0
x_80,1285 0
x_80

x_80,2277 0
x_80,2278 0
x_80,2279 0
x_80,2280 0
x_80,2281 0
x_80,2282 0
x_80,2283 0
x_80,2284 0
x_80,2285 0
x_80,2286 0
x_80,2287 0
x_80,2288 0
x_80,2289 0
x_80,2290 0
x_80,2291 0
x_80,2292 0
x_80,2293 0
x_80,2294 0
x_80,2295 0
x_80,2296 0
x_80,2297 0
x_80,2298 0
x_80,2299 0
x_80,2300 0
x_80,2301 0
x_80,2302 0
x_80,2303 0
x_80,2304 0
x_80,2305 0
x_80,2306 0
x_80,2307 0
x_80,2308 0
x_80,2309 0
x_80,2310 0
x_80,2311 0
x_80,2312 0
x_80,2313 0
x_80,2314 0
x_80,2315 0
x_80,2316 0
x_80,2317 0
x_80,2318 0
x_80,2319 0
x_80,2320 0
x_80,2321 0
x_80,2322 0
x_80,2323 0
x_80,2324 0
x_80,2325 0
x_80,2326 0
x_80,2327 0
x_80,2328 0
x_80,2329 0
x_80,2330 0
x_80,2331 0
x_80,2332 0
x_80,2333 0
x_80,2334 0
x_80,2335 0
x_80,2336 0
x_80,2337 0
x_80,2338 0
x_80,2339 0
x_80,2340 0
x_80,2341 0
x_80,2342 0
x_80,2343 0
x_80,2344 0
x_80,2345 0
x_80,2346 0
x_80,2347 0
x_80,2348 0
x_80,2349 0
x_80,2350 0
x_80,2351 0
x_80,2352 0
x_80,2353 0
x_80,2354 0
x_80,2355 0
x_80,2356 0
x_80,2357 0
x_80,2358 0
x_80,2359 0
x_80

x_81,878 0
x_81,879 0
x_81,880 0
x_81,881 0
x_81,882 0
x_81,883 0
x_81,884 0
x_81,885 0
x_81,886 0
x_81,887 0
x_81,888 0
x_81,889 0
x_81,890 0
x_81,891 0
x_81,892 0
x_81,893 0
x_81,894 0
x_81,895 0
x_81,896 0
x_81,897 0
x_81,898 0
x_81,899 0
x_81,900 0
x_81,901 0
x_81,902 0
x_81,903 0
x_81,904 0
x_81,905 0
x_81,906 0
x_81,907 0
x_81,908 0
x_81,909 0
x_81,910 0
x_81,911 0
x_81,912 0
x_81,913 0
x_81,914 0
x_81,915 0
x_81,916 0
x_81,917 0
x_81,918 0
x_81,919 0
x_81,920 0
x_81,921 0
x_81,922 0
x_81,923 0
x_81,924 0
x_81,925 0
x_81,926 0
x_81,927 0
x_81,928 0
x_81,929 0
x_81,930 0
x_81,931 0
x_81,932 0
x_81,933 0
x_81,934 0
x_81,935 0
x_81,936 0
x_81,937 0
x_81,938 0
x_81,939 0
x_81,940 0
x_81,941 0
x_81,942 0
x_81,943 0
x_81,944 0
x_81,945 0
x_81,946 0
x_81,947 0
x_81,948 0
x_81,949 0
x_81,950 0
x_81,951 0
x_81,952 0
x_81,953 0
x_81,954 0
x_81,955 0
x_81,956 0
x_81,957 0
x_81,958 0
x_81,959 0
x_81,960 0
x_81,961 0
x_81,962 0
x_81,963 0
x_81,964 0
x_81,965 0
x_81,966 0
x_81,967 0
x_81,968 0

x_81,2306 0
x_81,2307 0
x_81,2308 0
x_81,2309 0
x_81,2310 0
x_81,2311 0
x_81,2312 0
x_81,2313 0
x_81,2314 0
x_81,2315 0
x_81,2316 0
x_81,2317 0
x_81,2318 0
x_81,2319 0
x_81,2320 0
x_81,2321 0
x_81,2322 0
x_81,2323 0
x_81,2324 0
x_81,2325 0
x_81,2326 0
x_81,2327 0
x_81,2328 0
x_81,2329 0
x_81,2330 0
x_81,2331 0
x_81,2332 0
x_81,2333 0
x_81,2334 0
x_81,2335 0
x_81,2336 0
x_81,2337 0
x_81,2338 0
x_81,2339 0
x_81,2340 0
x_81,2341 0
x_81,2342 0
x_81,2343 0
x_81,2344 0
x_81,2345 0
x_81,2346 0
x_81,2347 0
x_81,2348 0
x_81,2349 0
x_81,2350 0
x_81,2351 0
x_81,2352 0
x_81,2353 0
x_81,2354 0
x_81,2355 0
x_81,2356 0
x_81,2357 0
x_81,2358 0
x_81,2359 0
x_81,2360 0
x_81,2361 0
x_81,2362 0
x_81,2363 0
x_81,2364 0
x_81,2365 0
x_81,2366 0
x_81,2367 0
x_81,2368 0
x_81,2369 0
x_81,2370 0
x_81,2371 0
x_81,2372 0
x_81,2373 0
x_81,2374 0
x_81,2375 0
x_81,2376 0
x_81,2377 0
x_81,2378 0
x_81,2379 0
x_81,2380 0
x_81,2381 0
x_81,2382 0
x_81,2383 0
x_81,2384 0
x_81,2385 0
x_81,2386 0
x_81,2387 0
x_81,2388 0
x_81

x_82,219 0
x_82,220 0
x_82,221 0
x_82,222 0
x_82,223 0
x_82,224 0
x_82,225 0
x_82,226 0
x_82,227 0
x_82,228 0
x_82,229 0
x_82,230 0
x_82,231 0
x_82,232 0
x_82,233 0
x_82,234 0
x_82,235 0
x_82,236 0
x_82,237 0
x_82,238 0
x_82,239 0
x_82,240 0
x_82,241 0
x_82,242 0
x_82,243 0
x_82,244 0
x_82,245 0
x_82,246 0
x_82,247 0
x_82,248 0
x_82,249 0
x_82,250 0
x_82,251 0
x_82,252 0
x_82,253 0
x_82,254 0
x_82,255 0
x_82,256 0
x_82,257 0
x_82,258 0
x_82,259 0
x_82,260 0
x_82,261 0
x_82,262 0
x_82,263 0
x_82,264 0
x_82,265 0
x_82,266 0
x_82,267 0
x_82,268 0
x_82,269 0
x_82,270 0
x_82,271 0
x_82,272 0
x_82,273 0
x_82,274 0
x_82,275 0
x_82,276 0
x_82,277 0
x_82,278 0
x_82,279 0
x_82,280 0
x_82,281 0
x_82,282 0
x_82,283 0
x_82,284 0
x_82,285 0
x_82,286 0
x_82,287 0
x_82,288 0
x_82,289 0
x_82,290 0
x_82,291 0
x_82,292 0
x_82,293 0
x_82,294 0
x_82,295 0
x_82,296 0
x_82,297 0
x_82,298 0
x_82,299 0
x_82,300 0
x_82,301 0
x_82,302 0
x_82,303 0
x_82,304 0
x_82,305 0
x_82,306 0
x_82,307 0
x_82,308 0
x_82,309 0

In [51]:
timetabling.write("file_infeasible.lp")
timetabling.write("file_infeasible.mps")